In [4]:
import os
import tensorflow as tf

# univariate cnn example
from keras.models import Sequential
from keras.layers import Dense
from keras.layers import Flatten
from keras.layers.convolutional import Conv1D
from keras.layers.convolutional import MaxPooling1D

import numpy as np
import pandas as pd
# from matplotlib import pyplot as plt

from keras.utils import Sequence
from keras.utils import to_categorical

In [5]:
training_dir = os.listdir('../Pp_Training_SetA/')
list_id = []
for file in training_dir:
    filename = os.fsdecode(file)
    id = filename.lstrip("p").rstrip('.csv')
    list_id.append(id)

In [6]:
df = pd.DataFrame()
for ID in list_id:
    with open(f'../Pp_Training_SetA/p{ID}.csv', 'r') as f:
        df_id = pd.read_csv(f)
        df = df.append(df_id)
df.head()

/var/folders/wq/mnv64xbs77b03n4b7s0w2w3h0000gn/T/ipykernel_14099/174141211.py:5: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append(df_id)
/var/folders/wq/mnv64xbs77b03n4b7s0w2w3h0000gn/T/ipykernel_14099/174141211.py:5: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append(df_id)
/var/folders/wq/mnv64xbs77b03n4b7s0w2w3h0000gn/T/ipykernel_14099/174141211.py:5: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append(df_id)
/var/folders/wq/mnv64xbs77b03n4b7s0w2w3h0000gn/T/ipykernel_14099/174141211.py:5: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append(df_id)
/var/folders/wq/mnv64xbs77b03n4b7s0w2w3h0000gn/T

HR     O2Sat      Temp  SBP       MAP  DBP      Resp  BaseExcess  \
0  1.160853  0.353553 -1.870829  0.0  1.532474  0.0  1.207615         0.0   
1  1.160853  0.353553 -1.870829  0.0  1.532474  0.0  1.207615         0.0   
2  1.160853  0.353553 -1.870829  0.0  1.532474  0.0  1.207615         0.0   
3  1.160853  0.353553 -1.870829  0.0  1.532474  0.0  1.207615         0.0   
4  1.160853  0.353553 -1.870829  0.0  1.532474  0.0  1.207615         0.0   

   HCO3  FiO2  ...  WBC  Fibrinogen  Platelets  Age  Gender  Unit1  Unit2  \
0   0.0   0.0  ...  0.0         0.0        0.0  0.0     1.0    1.0    0.0   
1   0.0   0.0  ...  0.0         0.0        0.0  0.0     1.0    1.0    0.0   
2   0.0   0.0  ...  0.0         0.0        0.0  0.0     1.0    1.0    0.0   
3   0.0   0.0  ...  0.0         0.0        0.0  0.0     1.0    1.0    0.0   
4   0.0   0.0  ...  0.0         0.0        0.0  0.0     1.0    1.0    0.0   

   HospAdmTime    ICULOS  SepsisLabel  
0          0.0 -1.428869          1.0  
1          0.0 -1.428869          1.0  
2          0.0 -1.428869          1.0  
3          0.0 -1.428869          1.0  
4          0.0 -1.428869          1.0  

[5 rows x 40 columns]

In [22]:
df = pd.read_csv('data.csv')
df.head

<bound method NDFrame.head of         Unnamed: 0        HR     O2Sat      Temp       SBP       MAP  \
0                0  1.160853  0.353553 -1.870829  0.000000  1.532474   
1                1  1.160853  0.353553 -1.870829  0.000000  1.532474   
2                2  1.160853  0.353553 -1.870829  0.000000  1.532474   
3                3  1.160853  0.353553 -1.870829  0.000000  1.532474   
4                4  1.160853  0.353553 -1.870829  0.000000  1.532474   
...            ...       ...       ...       ...       ...       ...   
989637          38 -1.483900 -0.796084 -2.835949 -1.135269 -1.539809   
989638          39 -1.907065  0.734847  0.118165 -1.062959 -1.231304   
989639          40 -1.907065  0.734847  0.118165 -1.062959 -1.231304   
989640          41  0.208762  0.734847  0.118165 -0.412168 -0.853900   
989641          42 -0.919679 -0.796084  0.118165  0.383244 -0.134056   

             DBP      Resp  BaseExcess  HCO3  ...       WBC  Fibrinogen  \
0       0.000000  1.207615    

In [23]:
X = df.iloc[:, 3:-1].values
y = df.iloc[:, -1].values

In [32]:
print(X.shape)
print(y.shape)

(989642, 37)
(989642,)


In [43]:
from sklearn.model_selection import train_test_split

#Data splitting
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.3, random_state=42) 
# X_train = X_train.reshape(X_train.shape[0], 37, 40).astype('float32')
# X_test = X_test.reshape(X_test.shape[0], 37, 40).astype('float32')
print(X_test.shape)
print(X_train.shape)

(296893, 37)
(692749, 37)


In [38]:
from keras.optimizers import Adam

def define_model(lr, num_classes):
    model = Sequential()
    model.add(Conv1D(filters=32, kernel_size=3, strides=1, padding='same', activation='relu', input_shape=(37, 40)))
    model.add(MaxPooling1D(pool_size=2))
    model.add(Conv1D(filters=64, kernel_size=3, strides=1, padding='same', activation='relu'))
    model.add(MaxPooling1D(pool_size=2))
    model.add(Conv1D(filters=128, kernel_size=3, strides=1, padding='same', activation='relu'))
    model.add(Flatten())
    model.add(Dense(128))
    model.add(Dense(num_classes))
    
    opt = Adam(learning_rate=lr)
    model.compile(optimizer=opt, loss='mse', metrics=['accuracy'])
    return model

In [40]:
# runnning the model

model = define_model(lr=1e-2, num_classes=2)

# fit model
history = model.fit(x_train, y_train, epochs=100, verbose=0)

ValueError: in user code:

    File "/Users/davidfandrei/opt/miniconda3/envs/tensorflow/lib/python3.10/site-packages/keras/engine/training.py", line 1249, in train_function  *
        return step_function(self, iterator)
    File "/Users/davidfandrei/opt/miniconda3/envs/tensorflow/lib/python3.10/site-packages/keras/engine/training.py", line 1233, in step_function  **
        outputs = model.distribute_strategy.run(run_step, args=(data,))
    File "/Users/davidfandrei/opt/miniconda3/envs/tensorflow/lib/python3.10/site-packages/keras/engine/training.py", line 1222, in run_step  **
        outputs = model.train_step(data)
    File "/Users/davidfandrei/opt/miniconda3/envs/tensorflow/lib/python3.10/site-packages/keras/engine/training.py", line 1023, in train_step
        y_pred = self(x, training=True)
    File "/Users/davidfandrei/opt/miniconda3/envs/tensorflow/lib/python3.10/site-packages/keras/utils/traceback_utils.py", line 70, in error_handler
        raise e.with_traceback(filtered_tb